In [1]:
import pegasus as pg
from readers import auto_reader
from filters import initial_qc

In [2]:
# adata = pg.read_input("MantonBM_nonmix_subset.h5sc")
adata = auto_reader("mc_tm", 11, 4)[2]
adata

2020-06-06 14:27:58,000 - pegasus - INFO - Time spent on 'read_input' = 2.68s.
Processed /Users/michaelalperovich/Documents/primes_storage/data/tabula_muris/droplet/Kidney-10X_P4_6/raw_gene_bc_matrices_h5.h5.
2020-06-06 14:28:00,803 - pegasus - INFO - Time spent on 'read_input' = 2.44s.
Processed /Users/michaelalperovich/Documents/primes_storage/data/tabula_muris/droplet/Kidney-10X_P7_5/raw_gene_bc_matrices_h5.h5.
2020-06-06 14:28:03,639 - pegasus - INFO - Time spent on 'read_input' = 2.49s.
Processed /Users/michaelalperovich/Documents/primes_storage/data/tabula_muris/droplet/Kidney-10X_P4_5/raw_gene_bc_matrices_h5.h5.
2020-06-06 14:28:04,484 - pegasus - INFO - Time spent on 'aggregate' = 0.50s.
Aggregated 3 files.


AnnData object with n_obs × n_vars = 2211840 × 54446 
    obs: 'Channel'
    var: 'gene_ids'
    uns: 'genome'

In [3]:
adata.X

<2211840x54446 sparse matrix of type '<class 'numpy.float32'>'
	with 15686838 stored elements in Compressed Sparse Row format>

In [4]:
adata.obs.head()

Channel
Kidney-10X_P4_6-AAACCTGAGAAACCAT  Kidney-10X_P4_6
Kidney-10X_P4_6-AAACCTGAGAAACCGC  Kidney-10X_P4_6
Kidney-10X_P4_6-AAACCTGAGAAACCTA  Kidney-10X_P4_6
Kidney-10X_P4_6-AAACCTGAGAAACGAG  Kidney-10X_P4_6
Kidney-10X_P4_6-AAACCTGAGAAACGCC  Kidney-10X_P4_6

In [5]:
adata.obs['Channel'].value_counts()

Kidney-10X_P7_5    737280
Kidney-10X_P4_5    737280
Kidney-10X_P4_6    737280
Name: Channel, dtype: int64

In [6]:
adata.var.head()

gene_ids
4933401J01Rik  ENSMUSG00000102693.1
Gm26206        ENSMUSG00000064842.1
Xkr4           ENSMUSG00000051951.5
Gm18956        ENSMUSG00000102851.1
Gm37180        ENSMUSG00000103377.1

In [7]:
adata.uns['genome']

'gencode.vM19'

In [8]:
pg.qc_metrics(adata, mito_prefix="mt-")

In [9]:
stats_samples, stats_genes = pg.get_filter_stats(adata)

In [10]:
stats_samples

kept  median_n_genes  median_n_umis  median_percent_mito  \
Channel                                                                     
Kidney-10X_P4_5   330          1811.0         3909.0             1.897263   
Kidney-10X_P7_5   440          2260.5         5769.0             1.383311   
Kidney-10X_P4_6   455          1810.0         3963.0             1.614011   

                   filt   total  median_n_genes_before  median_n_umis_before  \
Channel                                                                        
Kidney-10X_P4_5  736950  737280                      0                   0.0   
Kidney-10X_P7_5  736840  737280                      0                   0.0   
Kidney-10X_P4_6  736825  737280                      0                   0.0   

                 median_percent_mito_before  
Channel                                      
Kidney-10X_P4_5                         0.0  
Kidney-10X_P7_5                         0.0  
Kidney-10X_P4_6                         0.0

In [11]:
stats_genes

n_cells  percent_cells
gene                                 
4933401J01Rik        0            0.0
Marcksl1-ps4         0            0.0
Gm26259              0            0.0
Gm46401              0            0.0
Gm47507              0            0.0
...                ...            ...
Gm34149              0            0.0
5530400C23Rik        0            0.0
Gm25019              0            0.0
Gm23403              0            0.0
Gm21748              0            0.0

[30475 rows x 2 columns]

In [12]:
pg.violin(adata, keys = ['n_genes', 'n_counts', 'percent_mito'], by = 'passed_qc')

:Layout
   .Violin.I   :Violin   [passed_qc]   (n_genes)
   .Violin.II  :Violin   [passed_qc]   (n_counts)
   .Violin.III :Violin   [passed_qc]   (percent_mito)

In [13]:
pg.scatter(adata, 'n_genes', 'n_counts', color = 'passed_qc')

:NdOverlay   [passed_qc]
   :Scatter   [n_genes]   (n_counts,__color,count)

In [14]:
pg.scatter(adata, 'n_genes', 'percent_mito', color = 'passed_qc')

:NdOverlay   [passed_qc]
   :Scatter   [n_genes]   (percent_mito,__color,count)

In [15]:
#pg.filter_data(adata)
adata = initial_qc(adata, 100, 3)
adata

2020-06-06 14:28:46,911 - pegasus - INFO - After filtration, 8028/2211840 cells and 20879/20879 genes are kept. Among 20879 genes, 20138 genes are robust.


AnnData object with n_obs × n_vars = 8028 × 20879 
    obs: 'Channel', 'passed_qc', 'n_genes', 'n_counts', 'percent_mito', 'percent_ribo'
    var: 'gene_ids', 'n_cells', 'percent_cells', 'robust', 'highly_variable_features'
    uns: 'genome'

In [16]:
adata.obs['Channel'].value_counts()

Kidney-10X_P7_5    3151
Kidney-10X_P4_6    2507
Kidney-10X_P4_5    2370
Name: Channel, dtype: int64

In [17]:
pg.log_norm(adata)

2020-06-06 14:22:19,169 - pegasus - INFO - Time spent on 'log_norm' = 0.17s.


In [18]:
pg.highly_variable_features(adata, consider_batch = False)
#pg.correct_batch(adata, features = 'highly_variable_features')

2020-06-06 14:22:19,341 - pegasus - INFO - 2000 highly variable features have been selected.
2020-06-06 14:22:19,342 - pegasus - INFO - Time spent on 'highly_variable_features' = 0.16s.


In [19]:
pg.variable_feature_plot(adata)

:Overlay
   .NdOverlay.I :NdOverlay   [highly_variable_features]
      :Scatter   [mean]   (var,__color,id)
   .Curve.I     :Curve   [mean]   (hvf_loess,id)

In [ ]:
adata.var.loc[adata.var['highly_variable_features']].sort_values(by = 'hvf_rank').tail(10)

In [23]:
pg.pca(adata)

2020-06-06 14:24:45,036 - pegasus - INFO - PCA is done. Time spent = 1.14s.


In [24]:
coord_pc1 = adata.uns['PCs'][:, 0]
coord_pc1

array([ 0.04618066,  0.00910651, -0.01145275, ..., -0.0144765 ,
       -0.01001696, -0.00443614], dtype=float32)

In [25]:
adata.var.loc[adata.var['highly_variable_features']].index.values

array(['Sox17', 'Sulf1', 'Lactb2', ..., 'mt-Nd3', 'mt-Nd4', 'mt-Nd5'],
      dtype=object)

In [26]:
adata.obsm['X_pca'].shape

(8028, 50)

In [27]:
pg.neighbors(adata)

2020-06-06 14:24:46,452 - pegasus - INFO - Time spent on 'get_neighbors' = 1.19s.
2020-06-06 14:24:46,757 - pegasus - INFO - Time spent on 'calculate_affinity_matrix' = 0.30s.


In [28]:
print("Get {} nearest neighbors (excluding itself) for each cell.".format(adata.uns['pca_knn_indices'].shape[1]))
adata.uns['pca_knn_indices']

Get 99 nearest neighbors (excluding itself) for each cell.


array([[3745, 6054, 7938, ..., 1820, 4437, 5311],
       [3400, 4601, 2306, ..., 1818, 1003, 1204],
       [1846,  444, 5672, ...,  717, 6604, 4428],
       ...,
       [ 444, 5987, 2249, ..., 5343,   38,  277],
       [ 583, 5535, 7029, ..., 6470, 4413, 3393],
       [1681, 1000, 1574, ..., 7793, 8002, 1254]])

In [29]:
adata.uns['pca_knn_distances']

array([[19.597849 , 20.414892 , 21.184984 , ..., 31.245106 , 31.320803 ,
        31.324432 ],
       [ 4.220779 ,  5.2043076,  5.386427 , ...,  7.7124   ,  7.7176585,
         7.738499 ],
       [ 5.2261653,  5.3800864,  5.573745 , ...,  8.707327 ,  8.719    ,
         8.775913 ],
       ...,
       [ 5.97922  ,  6.215645 ,  6.22312  , ...,  8.667382 ,  8.688099 ,
         8.703213 ],
       [ 4.4419284,  4.8550763,  4.9326167, ...,  6.621203 ,  6.6212797,
         6.62353  ],
       [ 5.2795353,  5.505829 ,  5.538478 , ...,  7.820238 ,  7.832597 ,
         7.851965 ]], dtype=float32)

In [30]:
pg.louvain(adata)

2020-06-06 14:24:47,264 - pegasus - INFO - Time spent on 'construct_graph' = 0.32s.
2020-06-06 14:24:51,181 - pegasus - INFO - Louvain clustering is done. Get 18 clusters. Time spent = 4.24s.


In [31]:
adata.obs['louvain_labels'].value_counts()

1     1091
2      844
3      683
4      643
5      581
6      544
7      456
8      430
9      413
10     394
11     322
12     303
13     272
14     243
15     237
16     204
17     186
18     182
Name: louvain_labels, dtype: int64

In [32]:
pg.composition_plot(adata, by = 'louvain_labels', condition = 'Channel')

:Bars   [louvain_labels,Channel]   (value)

In [ ]:
pg.fitsne(adata)

In [ ]:
pg.embedding(adata, basis = 'fitsne', keys = ['louvain_labels', 'Channel'])

In [ ]:
pg.umap(adata)

In [ ]:
pg.embedding(adata, basis = 'umap', keys = ['louvain_labels', 'Channel'])

In [ ]:
pg.de_analysis(adata, cluster = 'louvain_labels', auc = False, t = True, fisher = False, mwu = False,
                temp_folder = "/tmp")

In [ ]:
marker_dict = pg.markers(adata)

In [ ]:
marker_dict['1']['up']

In [ ]:
pg.volcano(adata, cluster_ids = ['1'])

In [ ]:
pg.write_results_to_excel(marker_dict, "MantonBM_nonmix_subset.louvain_labels.de.xlsx")

In [ ]:
#celltype_dict = pg.infer_cell_types(adata, markers = 'human_immune', de_test = 't')
#cluster_names = pg.infer_cluster_names(celltype_dict)

In [ ]:
#adata.rename_categories('louvain_labels', cluster_names)

In [ ]:
pg.embedding(adata, basis = 'fitsne', keys = ['louvain_labels'], legend='data')

In [ ]:
pg.embedding(adata, basis = 'fitsne', keys = ['louvain_labels'], legend='data')

In [ ]:
marker_genes = ['Epcam', 'Krt18', 'Slc12a3', 'Lrp2', 'Cubn', 'Slc34a1', 'Pck1', 'Miox', 'Slc5a2', 'Slc7a13', 'Nphs1', 'Pecam1', 'Ptprc', 'Slc12a1', 'Aqp2', 'Acta2']

pg.dotplot(adata, keys = marker_genes, by = 'louvain_labels')

In [ ]:
pg.heatmap(adata, keys = marker_genes, by = 'louvain_labels')

In [ ]:
pg.violin(adata, keys = "Slc34a1", by = 'louvain_labels', width = 900, height = 450)

In [ ]:
pg.embedding(adata, basis = 'fitsne', keys = marker_genes)

In [ ]:
pg.write_output(adata, 'tutorial_results')